In [ ]:
import numpy as np
import csv

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int

In [ ]:
def CalculateMovements(AnnotData):
  SumMovements = 0
  SumDistances = 0
  NumElements = 0
  for cell_id in AnnotData.keys():
    prevx = AnnotData[cell_id][0].posx
    prevy = AnnotData[cell_id][0].posy
    SumDistances += np.sqrt(np.power(AnnotData[cell_id][-1].posx-prevx,2)+np.power(AnnotData[cell_id][-1].posy-prevy,2))
    for element in AnnotData[cell_id]:
      SumMovements += np.sqrt(np.power(element.posx-prevx,2)+np.power(element.posy-prevy,2))
      NumElements += 1
      prevx = element.posx
      prevy = element.posy
  SumMovements /= NumElements
  SumDistances /= NumElements
  return [SumMovements, SumDistances]

In [ ]:
def ReadData(CellType, HumanDataFolder, ComputerDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  ComputerAnnotPath = ComputerDataFolder+CellType+"trajectories.txt"

  HumanAnnotFile = open(HumanAnnotPath,"r") 
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 

  HumanAnnotList = HumanAnnotFile.readlines()
  ComputerAnnotList = ComputerAnnotFile.readlines()

  HumanAnnotData = {}
  ComputerAnnotData = {}

  for row in HumanAnnotList:
    splitted = row.split(' ')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.posx = int(splitted[0])
      cellp.posy = int(splitted[1])
      cellp.frame = int(splitted[2])
      cellp.id = int(splitted[3].strip())
      if not (cellp.id in HumanAnnotData):
        HumanAnnotData[cellp.id]=[]
        HumanAnnotData[cellp.id].append(cellp)
      else:
        HumanAnnotData[cellp.id].append(cellp)

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.frame = int(splitted[0].strip())
      cellp.id = int(splitted[1].strip())
      cellp.posx = int(splitted[2].strip())
      cellp.posy = int(splitted[3].strip())
      if not (cellp.id in ComputerAnnotData):
        ComputerAnnotData[cellp.id]=[]
        ComputerAnnotData[cellp.id].append(cellp)
      else:
        ComputerAnnotData[cellp.id].append(cellp)

  return[HumanAnnotData, ComputerAnnotData]
  print("Successfull reading")
      

In [ ]:

CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/02 Human Annotations/"
ComputerDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/03 Estimated Paths/"
OutCSVPath = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Calculations.csv"

with open(OutCSVPath, mode='w') as CSVfile:
  CSVwriter = csv.writer(CSVfile, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
  CSVwriter.writerow(['CellType','HumanAnnotatedMovements','HumanAnnotatedDistances','ComputerAnnotatedMovements','ComputerAnnotatedDistances'])
  for CellType in CellTypes:
    #Reading both files
    [HumanAnnotData, ComputerAnnotData] = ReadData(CellType,HumanDataFolder,ComputerDataFolder)

    #Calculating the movements for both data
    [HumanSumMovements, HumanSumDistances] = CalculateMovements(HumanAnnotData)
    [ComputerSumMovements, ComputerSumDistances] = CalculateMovements(ComputerAnnotData)

    print(CellType)
    print("  "+str(HumanSumMovements))
    print("  "+str(HumanSumDistances))
    print("  "+str(ComputerSumMovements))
    print("  "+str(ComputerSumDistances))
    print()

    CSVwriter.writerow([CellType,HumanSumMovements,HumanSumDistances,ComputerSumMovements,ComputerSumDistances])

    

BIBF_01_7
  11.190917235821432
  2.3859413722115255
  8.676230278139109
  2.982823299195311

aktivin01_2
  4.17989340099444
  0.903030680902172
  3.8270553673758547
  1.0935113353505055

aktivin01_3
  4.107976087601958
  0.9315403970690852
  3.0132231442972497
  0.8998498326915808

hipox03_2
  1.6815014039135314
  0.45705310420196893
  3.305689747913437
  0.5869922070094917

melanoma_GF01_11
  3.201627352336034
  0.6335009825034801
  3.2315149468572444
  0.7246636467517824

zometa01_4
  1.8354768844580094
  0.29626376185641334
  3.548469971791256
  0.7691467570876593

